In [34]:
### IMPORT STATEMENTS ###

import torch
import torch.nn as nn
import torch.optim as optim
from torch.autograd import Variable
import numpy as np
import pandas as pd
import os
import time
import matplotlib.pyplot as plt
import string
from models import *
from configs import cfg
from nltk.translate.bleu_score import sentence_bleu, SmoothingFunction

In [51]:
### HELPER FUNCTIONS ###

# returns a pandas dataframe of the given file
# fname: string; path to the file
# num_rows: int; number of rows to read (for partial datasets)
# return: pandas Dataframe
def load_data(fname, num_rows = None):
    return pd.read_csv(fname, nrows = num_rows)


# creates a one-hot encoding matrix for the given data
# data: 1d numpy array; list of items/features to encode
# dictionary: dict; mapping from the item to its index
# return: 2d numpy array
def encode_one_hot(data, dictionary):
    # creates the 2d array of zeros
    one_hot_encoding = np.zeros((data.shape[0], len(dictionary)))
    
    # gathers the respective indices of each item
    data_indices = [dictionary[item] for item in data]

    # encodes the 1 for all the items
    one_hot_encoding[range(data.shape[0]), data_indices] = 1
    
    return one_hot_encoding


# converts a one-hot encoding of the reviews into strings
# data: 2d list; list of one-hot encoding
# dictionary: dict; mapping from the index to the character
# return: review strings (1d list)
def decode_one_hot_reviews(data):
    decoded = [''.join([cfg['valid_char'][torch.argmax(c)] 
                if torch.argmax(c) < cfg['valid_char_len'] 
                else '' for c in review]) for review in data]
    
    return decoded


# cleans and processes (feature encoding) the training data
# orig_data: pandas Dataframe; raw data that is outputted from load_data
# returns: features (2d numpy array; one-hot), labels (1d numpy array of strings), beer dictionary (dict)
def process_train_data(orig_data):
    print ("Processing training data")
    print ("Original data shape: " + str(orig_data.shape))
    
    # takes the relevant columns
    data = orig_data[['beer/style', 'review/overall', 'review/text']].copy()
    
    # --- DATA CLEANING ---
    
    # drops the rows with missing data
    data.replace('', np.nan, inplace = True)
    data.dropna(inplace = True)
    data.reset_index(drop = True, inplace = True)

    # sets all characters to lower case
    data['beer/style'] = data['beer/style'].str.lower()
    data['review/text'] = data['review/text'].str.lower()

    # converts all whitespace (space, tabs, newlines, etc.) into spaces
    whitespace_regex = '[' + string.whitespace + ']'
    data['review/text'] = data['review/text'].str.replace(whitespace_regex, ' ', regex = True)

    # removes all invalid characters
    invalid_char_regex = '[^' + cfg['valid_char'] + ']'
    data['review/text'] = data['review/text'].str.replace(invalid_char_regex, '', regex = True)
    
    print ("Data shape after cleaning: " + str(data.shape))
    
    # --- DATA PROCESSING ---
    
    # creates a list of beer and a dictionary to map a beer style to an index
    beer_list = data['beer/style'].unique()
    beer_to_index = dict(zip(beer_list, range(beer_list.shape[0])))
    print ("Number of unique beers: " + str(beer_list.shape[0]))

    # creates the input features
    beer_encoding = encode_one_hot(data['beer/style'].values, beer_to_index)
    score_encoding = data['review/overall'].values
    score_encoding = score_encoding.reshape(score_encoding.shape[0], 1)
    input_features = np.hstack((beer_encoding, score_encoding))
    print ("Input feature matrix shape: " + str(input_features.shape))
    
    # creates the labels
    labels = data['review/text'].values
    print ("Labels matrix shape: " + str(labels.shape))
    
    return input_features, labels, beer_to_index


# updates the configurations based on the results of the processed dataset
def update_configurations(feature_length):
    # sets the models' input dimensions to the size of features (beer style + score) + character encoding
    cfg['input_dim'] = feature_length + cfg['output_dim']

    
# splits the dataset + labels into a training and validation set
# features: numpy array
# labels: numpy array
# percent_training: float; percentage (from 0.0 to 1.0) of data to be used for training
# returns: training features, training labels, validation features, validation labels (all numpy arrays)
def train_valid_split(features, labels, percent_training):
    # gets the index of where to split
    training_last_index = int(percent_training * features.shape[0])

    x_train = features[:training_last_index]
    y_train = labels[:training_last_index]

    x_valid = features[training_last_index:]
    y_valid = labels[training_last_index:]
    
    print ("Training set size: " + str(x_train.shape[0]))
    print ("Validation set size: " + str(x_valid.shape[0]))
    
    return x_train, y_train, x_valid, y_valid
    

# cleans and processes (feature encoding) the testing data
# orig_data: pandas Dataframe; raw data that is outputted from load_data
# dictionary: dict; mapping from the beer style to its index (output of process_train_data)
# returns: features (2d numpy array; one-hot)
def process_test_data(orig_data, dictionary):  
    print ("Processing the testing data")
    print ("Original data shape: " + str(orig_data.shape))
    
    # takes the relevant columns
    data = orig_data[['beer/style', 'review/overall']]
    
    # --- DATA CLEANING ---
    
    # sets all characters to lower case
    data['beer/style'] = data['beer/style'].str.lower()
    
    # --- DATA PROCESSING ---
    
    # creates the input features
    beer_encoding = encode_one_hot(data['beer/style'].values, dictionary)
    score_encoding = data['review/overall'].values
    score_encoding = score_encoding.reshape(score_encoding.shape[0], 1)
    input_features = np.hstack((beer_encoding, score_encoding))
    print ("Input feature matrix shape: " + str(input_features.shape))
        
    return input_features


# pads the reviews so that all reviews in the set have an equal size
# and adds the <SOS> and <EOS> tags to the beginning and end of the reviews
# orig_data: 2d list of ints; list of reviews with the characters converted to their respective indices
# outputs: 2d numpy array of ints; padded reviews with the characters as indices
def pad_data(orig_data):
    # defines the character indices for the <SOS>, <EOS>, and <PAD> tags
    sos_tag_index = cfg['valid_char_len']
    eos_tag_index = sos_tag_index + 1
    pad_tag_index = eos_tag_index + 1
    
    # finds the longest review length
    review_lengths = [len(review) for review in orig_data]
    longest_review_length = np.max(review_lengths)
    
    # pads the reviews and adds the <SOS> and <EOS> tags
    padded_reviews = []
    for review in orig_data:
        pad_length = longest_review_length - len(review)
        padded_review = [sos_tag_index] + review + [eos_tag_index] + [pad_tag_index] * pad_length
        padded_reviews.append(padded_review)
        
    return np.array(padded_reviews)


def train(model, model_name, criterion, optimizer, computing_device, x_train, y_train, x_valid, y_valid, cfg):
    train_loss = []
    valid_loss = []
    valid_bleu = []

    start_time = time.time()
    
    softmax = nn.LogSoftmax(dim = 1)
    bleu_smoothing = SmoothingFunction()
    
    early_stop_count = 0
    min_loss = 100

    for epoch in range(1, cfg['epochs'] + 1):

        print ('----- Epoch #' + str(epoch) + ' -----')

        start_index = 0
        end_index = cfg['batch_size']

        losses = []

        print ('----- Training -----')
        while start_index < len(x_train):
            # takes the minibatch subset
            batch_x = x_train[start_index:end_index]
            batch_y = y_train[start_index:end_index]

            # converts the reviews char -> index
            indexed_reviews = [[char_to_index[c] for c in review] for review in batch_y]

            # pads the reviews
            padded_reviews = pad_data(indexed_reviews)

            # converts the review to a one-hot encoding
            # and concatenates this to the input features
            one_hot_length = cfg['output_dim']
            final_batch_x = []
            for features, reviews in zip(batch_x, padded_reviews):
                for char_index in reviews:
                    one_hot_encoding = np.zeros(one_hot_length)
                    one_hot_encoding[char_index] = 1
                    final_features = np.hstack((features, one_hot_encoding))
                    final_batch_x.append(final_features)

            # converts the final array into a numpy array
            final_batch_x = np.array(final_batch_x)

            # resizes the flattened array into batch_size x sequence_length x feature_length
            final_batch_x.resize(padded_reviews.shape[0], padded_reviews.shape[1], final_batch_x.shape[1])

            # converts final input array to tensor
            final_batch_x = torch.from_numpy(final_batch_x).float().to(computing_device)

            # zeros the gradients
            optimizer.zero_grad()

            # passes the final input array to the model's forward pass
            outputs, _ = model(final_batch_x)
            soft_outputs = softmax(outputs)

            # prints the actual reviews vs the predicted reviews
            actual_reviews = batch_y
            predicted_reviews = decode_one_hot_reviews(soft_outputs)
            
            for i in range(1):
                print ("Actual Review: " + actual_reviews[i])
                print ("Predicted Review: " + predicted_reviews[i])
            
            # reshapes the outputs to N x feature_length (for the loss function)
            outputs = outputs.view(-1, outputs.shape[2])

            # creates the targets and reshapes it to a single dimension
            targets = torch.from_numpy(padded_reviews).long()
            targets = targets.view(-1)

            # passes the outputs and targets to the loss function and backpropagates
            loss = criterion(outputs, targets)
            loss.backward()
            optimizer.step()

            losses.append(loss.item())

            print("Batch start index: " + str(start_index) + " | Loss: " + str(loss.item()))
            print("Time elapsed: " + str(time.time() - start_time))

            start_index = end_index
            end_index += cfg['batch_size']
            
            # stops training when the remaining data count is less than a minibatch
            if end_index > len(x_train):
                break


        train_loss.append(np.mean(losses))
        torch.save(model, model_name + "_e" + epoch + ".pt")
        print()

        print ('----- Validating -----')
        start_index = 0
        end_index = cfg['batch_size']

        losses = []
        bleus = []

        with torch.no_grad():

            while start_index < len(x_valid):
                # takes the minibatch subset
                batch_x = x_valid[start_index:end_index]
                batch_y = y_valid[start_index:end_index]

                # converts the reviews char -> index
                indexed_reviews = [[char_to_index[c] for c in review] for review in batch_y]

                # pads the reviews
                padded_reviews = pad_data(indexed_reviews)

                # converts the review to a one-hot encoding
                # and concatenates this to the input features
                one_hot_length = cfg['output_dim']
                final_batch_x = []
                for features, reviews in zip(batch_x, padded_reviews):
                    for char_index in reviews:
                        one_hot_encoding = np.zeros(one_hot_length)
                        one_hot_encoding[char_index] = 1
                        final_features = np.hstack((features, one_hot_encoding))
                        final_batch_x.append(final_features)

                # converts the final array into a numpy array
                final_batch_x = np.array(final_batch_x)

                # resizes the flattened array into batch_size x sequence_length x feature_length
                final_batch_x.resize(padded_reviews.shape[0], padded_reviews.shape[1], final_batch_x.shape[1])

                # converts final input array to tensors
                final_batch_x = torch.from_numpy(final_batch_x).float().to(computing_device)

                # passes the final input array to the model's forward pass
                outputs, _ = model(final_batch_x)
                soft_outputs = softmax(outputs)
                
                # prints the actual reviews vs the predicted reviews
                actual_reviews = batch_y
                predicted_reviews = decode_one_hot_reviews(soft_outputs)
                
                for a, p in zip(actual_reviews, predicted_reviews):
                    bleus.append(sentence_bleu(a.split(), p.split(), smoothing_function = bleu_smoothing.method1))
                    
                for i in range(1):
                    print ("Actual Review: " + actual_reviews[i])
                    print ("Predicted Review: " + predicted_reviews[i])


                # resizes the outputs to N x feature_length (for the loss function)
                outputs = outputs.view(-1, outputs.shape[2])

                # creates the targets and reshapes it to a single dimension
                targets = torch.from_numpy(padded_reviews).long()
                targets = targets.view(-1)

                # passes the outputs and targets to the loss function
                loss = criterion(outputs, targets)

                losses.append(loss.item())

                print("Batch start index: " + str(start_index))
                print("Loss: " + str(loss.item()) + " | BLEU score: " + str(np.mean(valid_bleu)))
                print("Time elapsed: " + str(time.time() - start_time))

                start_index = end_index
                end_index += cfg['batch_size']
                
                # 
                if end_index > len(x_valid):
                    break


        average_loss = np.mean(losses)
        valid_loss.append(average_loss)
        valid_bleu.append(np.mean(bleus))
        
        print()

        # checks for early stopping when the validation loss is higher for x consecutive epochs
        if average_loss >= min_loss:
            early_stop_count += 1

            if early_stop_count >= cfg['early_stop']:
                break

        else:
            early_stop_count = 0
            min_loss = average_loss
            
    return train_loss, valid_loss, valid_bleu
    
    
def process_results(model_name, train_loss, valid_loss, valid_bleu):
    # summarizes the results
    print (model_name + " Results:")
    print ("Training Loss: " + str(train_loss))
    print ("Validation Loss: " + str(valid_loss))
    print ("Validation Bleu Score: " + str(valid_bleu))

    # graphs the loss curves
    plt.plot(range(len(train_loss)), train_loss, 'b--', label = 'Training Loss')
    plt.plot(range(len(valid_loss)), valid_loss, 'r--', label = 'Validation Loss')

    plt.grid(True)
    plt.xlabel("Epoch")
    plt.ylabel("Loss")
    plt.title(model_name + " Loss Curve")
    plt.legend(loc="upper right")

    plt.savefig(model_name + " Loss.png")
    
    # graphs the bleu score curve
    plt.plot(range(len(valid_bleu)), valid_bleu, 'r--', label = 'Validation Bleu Score')
    
    plt.grid(True)
    plt.xlabel("Epoch")
    plt.ylabel("Bleu Score")
    plt.title(model_name + " Bleu Score Curve")
    plt.legend(loc="lower right")

    plt.savefig(model_name + " Bleu Score.png")
    
    
def generate(model, X_test, cfg):
    # TODO: Given n rows in test data, generate a list of n strings, where each string is the review
    # corresponding to each input row in test data.
    raise NotImplementedError
    
    
def save_to_file(outputs, fname):
    # TODO: Given the list of generated review outputs and output file name, save all these reviews to
    # the file in .txt format.
    raise NotImplementedError


In [52]:
### MAIN FUNCTION ###

train_data_fname = "Beeradvocate_Train.csv"
test_data_fname = "Beeradvocate_Test.csv"
out_fname = "Output_Reviews.txt"

# loads the data
train_data = load_data(train_data_fname, cfg['num_data'])
#test_data = load_data(test_data_fname, cfg['num_data'])

# processes the data to get the train, valid, and test sets
train_data, train_labels, beer_to_index = process_train_data(train_data)
x_train, y_train, x_valid, y_valid = train_valid_split(train_data, train_labels, cfg['train_percentage'])
#x_test = process_test_data(test_data, beer_to_index)

# updates the configurations based on the processed data
update_configurations(x_train.shape[1])

# creates the dictionaries to map a character to its index in a one-hot encoding
char_to_index = dict(zip(list(cfg['valid_char']), range(cfg['valid_char_len'])))

# gets the computing device (either cuda or cpu)
if torch.cuda.is_available():
    computing_device = torch.device("cuda")
    cfg['cuda'] = True
    
else:
    computing_device = torch.device("cpu")
    cfg['cuda'] = False

Processing training data
Original data shape: (5000, 14)
Data shape after cleaning: (4999, 3)
Number of unique beers: 78
Input feature matrix shape: (4999, 79)
Labels matrix shape: (4999,)
Training set size: 3999
Validation set size: 1000


'\ntrain(model, X_train, y_train, X_valid, y_valid, cfg) # Train the model\noutputs = generate(model, X_test, cfg) # Generate the outputs for test data\nsave_to_file(outputs, out_fname) # Save the generated outputs to a file\n'

In [ ]:
# defines the hyperparameters
model_number = 1

cfg['hidden_dim'] = 32
cfg['layers'] = 1

In [ ]:
# trains the LSTM model
model = bLSTM(cfg).to(computing_device)
optimizer = optim.Adam(model.parameters(), cfg['learning_rate'])
criterion = nn.CrossEntropyLoss()

train_loss, valid_loss, valid_bleu = train(model, "LSTM" + str(model_number), criterion, optimizer, computing_device, 
                                           x_train, y_train, x_valid, y_valid, cfg)

process_results("LSTM Model " + str(model_number), train_loss, valid_loss, valid_bleu)

----- Epoch #1 -----
----- Training -----
Actual Review: a lot of foam. but a lot. in the smell some banana, and then lactic and tart. not a good start. quite dark orange in color, with a lively carbonation (now visible, under the foam). again tending to lactic sourness. same for the taste. with some yeast and banana.
Predicted Review: llll'''',l,.'j56luj''ll6,5l'jlju''lj'''ll6j''l'.'.-gl-.16ju'.'''',''l'.'6j''50qj.1''ll6.16l5''50'$u'5'''''$66''1''''jl'.'.''ll'5.l'll'6'''6'''l.1.1'.16j116665l5ll''lu.''''ju'',.'j'56-''5.lj''''.'lj.''''5''ll6g'.''l5lloj''56''ju''j'l5'''''5.ll6j''''''5''.''l'.'1--0,,,e7777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777777

Batch start index: 96 | Loss: 3.8296239376068115
Time elapsed: 13.705153942108154
Actual Review: got a can of caldera pale ale from a neighbor that collects cans, but did not really like the beer. you have to love a nice pale ale in a can. the beer is a cloudy yellow with a nice head that fell after a couple of minutes. the smell is very malty for a apa and has a nice hint of floral hops. the taste is very well balance between malt and hops. not overly bitter or hoppy, but right on for a pale ale. this a a very good interpretation of the style and unique with the nice malt presence. mouthfeel is on the medium side and the drinkability is good a well. this woould make a very good session beer if it were regularly available to me. i would definitely recommend this beer if you are looking for an above average pale ale.
Predicted Review: l''8l'o''566oo''o''oo6oo'o'''oo'ojooo5''oll6165)q26q '''5lo''5llolu5oo5o65656''o'''o''6'o56'ol'''06'6uo6')'o566'o)'o'o55'o6'''o'''o'5o'o'50656'6l'''o'looo

Batch start index: 224 | Loss: 3.773538827896118
Time elapsed: 26.18300986289978
Actual Review: 22 oz bomber to pint glass  pours a rich reddish-brown that, although isn't cloudy or murky, is dark enough to let little light through. it's seems to be amply carbonated, but the small head quickly dissipates leaving little lacing.  the nose is a little flat. given the description on the bottle, i was expecting something unique and layered, but i could have mistaken this for newcastle (sorry nc fans). you can pick up a bit of the orange, but given that the label mentions orange was added, you're smelling for it.  the flavors are a bit more pronounced than the scent, but they're perhaps less interesting. you're met with roasted malts and orange, but the flavors don't pop, at all, and they're combined with muddy, earthy tones that becomes cloyingly sweet as the sip progresses. this beer needs something else. hops, perhaps? perhaps not, it's simply unbalanced.  given the wispy head, i wasn't e

Batch start index: 352 | Loss: 3.7653143405914307
Time elapsed: 37.51052403450012
Actual Review: a - pours a hazy burnt orange. a billowy 3 finger head. average lacing.  s - big citrus aroma, caramel, hints of alcohol, dried herbs.  t - citrus hops with some strawberry fruitiness. some floral spice in the back fades into toasted caramel malt. the malt has a nice sweetness that keeps the hops from taking over everything.   the malt seems shy at first but opens up as you go. my first ipa out of a can. very easy drinking. good stuff!
Predicted Review: ''l'o66u''6o66o6u66uq.h661-16u06o665o5olu6l6o55o''66uoq06-6qq-o'6'o55l066l6ool5o66'5'ul6o'6jol661-ju6l666.5l66o6oo66 6l6q15'q66uq$u066566655'ul6666u6l5566l6ju6'5'oelu'qu6o'uo55'''56'oj'6ooo'o56'65'6'5656u6u6q$6oo''6555656'5'66'q-ju66uoo55656u6u655666l6o665'6'e''5''''o56o566uu6'656u6666u6o'oj65$51666)qq6u6'quh 116066656u6u6o56'''u'o'6u6'56o5''56lu5666u6'6u66o'o'6u6o656uu6o5''5656o66u566o6o66'6066qqu6uo'u66q5.$51606666.6l5uoo555,,777aaaaaaaaaa

Batch start index: 480 | Loss: 3.612912654876709
Time elapsed: 51.641438245773315
Actual Review: a: pours a hazy orangereddish with a soapy, foamy head. lots of bubbles of small carbonation.  s: pine, citrus, and grapefruit all the way, almost to the point of smelling like a fresca! (how's that for an obscure reference). the malt is also noticeable in the form of a little fruitness.  t: wow! the hops pack a whallop both in the nose and in the finish of the taste, but the sweet malt coats the tongue and the throat and balances out nicely. the aftertaste of so many hops does take down the mouthfeel a bit, but the taste is definitely...tasty!!!  m: the hops sting a bit, even in the mouthfeel, but the malt is moderately thick, which helps wash everything down. the only drawback i can see is that the hops stick around so much in the aftertaste. it wants me to drink more, but it still is a little surprising.  d: this is a good ipa. almost like a firestone pale ale supercharged; the hops are 

...

Batch start index: 3552 | Loss: 1.3054410219192505
Time elapsed: 1225.954928636551
Actual Review: 22oz bomber courtesy of alexsdad06 poured into a snifter.  pours like motor oil out of the bottle with a small mocha head that leaves a thin collar and some drippy lacing.  the aroma is massively roasty with lots of black malts, cocoa powder, bakers chocolate and espresso. there is a hop presence but not enough to take away from the deeply roasted malt dominance.  more dark chocolate and charred black malts in the taste. the hops are a little more present and there is a bitterness in the finish that is half citrus hops and half bitter chocolate. there are some dark sweet fruits and licorice hiding behind the malts as well.  the mouthfeel is medium bodied and ultra smooth with the oatmeal adding to of the body. dessert-like.  this beer is not fooling around - massively roasted with lots of malts, hops and sugary sweetness in the background. definitely a sipper and probably not quite as good

Batch start index: 3680 | Loss: 1.1839308738708496
Time elapsed: 1241.1372368335724
Actual Review: poured a black color with a large frothy brown head that lasted with excellent lacing. moderate to heavy toasted chocolate, caramel and alcohol aroma. heavy bittersweet toasted black malt flavor with a heavy bittersweet and small alcohol bite finish of long duration. full body with a smooth texture and flat carbonation. this is a standout beer.
Predicted Review: !6bubbddndb'ndqd6q'''6w'tddndsnbw'dj'bndddvvbwndddnddnhntdsnsnndduvthddddd'l'snsln6'su6ddbddbbtndtndddnvddnbnnnnddddddb'btnnddbbbvnlsnnddnl6'd6'snbb!nbdddnvddvbttnbswunndtnnnnnddv'ndqddnltsdlnvbbdwbthdndddnvddvbttnbswunndnnddsdnnlsnl''66's''nnsj'n's6d66d'os66duvbtbbndddu'ls''d6dwvthdndsdbbnddnddtuvddnnddd'ntsdbbbbnntbbnddnhvsdwssnssnnndbundbnnbbbttttii
Batch start index: 3712 | Loss: 1.4781047105789185
Time elapsed: 1244.1754961013794
Actual Review: 22oz bottle served in a snifter. no freshness info.  pours a completely opaque jet

Batch start index: 3808 | Loss: 1.7347688674926758
Time elapsed: 1252.4507596492767
Actual Review: appearance: pours a dark orange color with a short 12 head that breaks apart quickly. some mild lacing develops.  smell: some citrus, caramel, and fruitiness sweetness are mild on the nose.  taste: caramel, mild citrus, fruit sweetness, decent bitterenss, and a bit of breadiness makes up a mellow ipa. this is a bit thinner than expected on the malt presence.   mouthfeel: lightly crisp throughout. a bit dry at the finish. thinner side of a medium bodied beer. aftertaste is short.  drinkability: decent ipa, but not one i would want to make a session beer. worth a look.
Predicted Review: !vvpdbbbnddvddduvndnddbbvvbbbbwud6q'''qw'thdndsddbbdqddhdnddnhntdvvbbbndndbbtdquv6q'qqds6!'ddbl'dl'6's6dddvb'o6s6ddsju'l'6s'!'d6'tbusuddbbbvnl'dnndddvubtbnnssssuuunnnnsdnbbddbl'd6ndnhddudnudddnnntnvddbbbvn''dj'l'd6'tbusudd'ubtssuuunnnnsudddddnndvbtttbnnssudnnddndvbtdd6d'bbbdbnnnsdjnbbndu6dnddd'l''s'6bbdthvsd

Actual Review: a dark yellow in color a little hazy. it had a small head that kind of disappeared.  s you smell the pumpkin and cinnamon in this one nice nose.  t decent taste the pumpkin didn't come out as much as i hoped for but decent.  m limited carbonation in this beer kind of hurt the beer made it oily.  d the drinkability was decent wouldn't want more than one from this style of beer period. hoppin' frog's was good but i liked southern tier's better.
Predicted Review: 'vvdbbbv)u'l''s'sdd6'o'qnsl'ttlosdnv)qdbtdhnddndsdnnlshunddthntdvbnddddddbnn66dnbbdbddsdu6udsju'lsshudduddvbndnndddvnnnvbndbndnhvsd6nudwb6udubnnbddndddddntdtnntndthddduddvbnddbdnvndddddddundnnsdudddnsdbshddddddbbvbundddddntddddds'!'tndddbbbbnntbbnd'ndnhvsdwnnb)q'bddd6dduvtdthddvunbvjndndbtsdblyqddddnhdddvbnvbbblllydunssduddntdudu'dn6ndwnntdddbbdnhnnddnuddbbvdthbsdsnul'do6d'nnb)6ubbbdbdhdddvn6d6bb66nswnnsu6bddbundbsl'''ddsoundubndnbnb'ss''ntnbbbtta9
Batch start index: 96
Loss: 1.3742576837539673 | BLEU score: 0.0054

Actual Review: 2009 vintage. saw this today and wondered how it slipped through the cracks. rated accordingly (i.e. taking age into account).  appearance  pours a hazy golden color into a tulip. about a finger  of white head is achieved with a regular pour that dissipates quickly leaving just splotches of lacing on the sides of the glass.  smell  despite being two years old, plenty of spices associated with pumpkin pie such as nutmeg and cinnamon. as the beer warms some allspice is detected. a definite pumpkin aroma also.  taste  not as strong as the nose, but was perhaps as expected due to the age. a bit of a malty forward flavor that is mixed with the spices. i taste clove and cinnamon more than anything. slight pumpkin, brown sugar, and vanilla.  mouthfeel  medium bodied, decent carbonation.  overall  a solid pumpkin beer. coincidentally i probably like this with age on it. ill have to pick up a fresher one to see how it compares, but this has held up surprisingly well.
Predicted Re

In [13]:
# trains the GRU model
model = bGRU(cfg).to(computing_device)
optimizer = optim.Adam(model.parameters(), cfg['learning_rate'])
criterion = nn.CrossEntropyLoss()

train_loss, valid_loss, valid_bleu = train(model, "GRU" + str(model_number), criterion, optimizer, computing_device, 
                                           x_train, y_train, x_valid, y_valid, cfg)

process_results("GRU Model " + str(model_number), train_loss, valid_loss, valid_bleu)

----- Epoch #1 -----
----- Training -----
Actual Review: a lot of foam. but a lot. in the smell some banana, and then lactic and tart. not a good start. quite dark orange in color, with a lively carbonation (now visible, under the foam). again tending to lactic sourness. same for the taste. with some yeast and banana.
Predicted Review: )uu w 9w w wwwuu8ww9ww w u9uww   9  w  9 w ww8wwwww uwwww   ww wu  uuwwww ww uuww 9wwwwwww  ww uurww  wwww uwwwwwwwwwwww w  uuu  9ww  uw  9uwwuwww  wwwwww uuu  u wuuwwwwww   9 www  uwwwwww www ww9 w9 wu  uuwwwwww  uu wwww ww9   9 w  wuuuu  9 w ww ww  9wwwwuwwwwwuuuuunee,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,,

Batch start index: 96 | Loss: 3.9466140270233154
Time elapsed: 6.624752044677734
Actual Review: got a can of caldera pale ale from a neighbor that collects cans, but did not really like the beer. you have to love a nice pale ale in a can. the beer is a cloudy yellow with a nice head that fell after a couple of minutes. the smell is very malty for a apa and has a nice hint of floral hops. the taste is very well balance between malt and hops. not overly bitter or hoppy, but right on for a pale ale. this a a very good interpretation of the style and unique with the nice malt presence. mouthfeel is on the medium side and the drinkability is good a well. this woould make a very good session beer if it were regularly available to me. i would definitely recommend this beer if you are looking for an above average pale ale.
Predicted Review: u)h69w99ww99699w   hw99w  9w  96hh 9w9ww jv29h96v 6999   w6 99ww  9u9v9   9w9699ww   9  n:9vvs98mm9.9v999vv w9v99 h w9w9w uw99w  9w  9v 9w99ww.96v 98mw99  

Batch start index: 224 | Loss: 3.9040610790252686
Time elapsed: 12.76993179321289
Actual Review: 22 oz bomber to pint glass  pours a rich reddish-brown that, although isn't cloudy or murky, is dark enough to let little light through. it's seems to be amply carbonated, but the small head quickly dissipates leaving little lacing.  the nose is a little flat. given the description on the bottle, i was expecting something unique and layered, but i could have mistaken this for newcastle (sorry nc fans). you can pick up a bit of the orange, but given that the label mentions orange was added, you're smelling for it.  the flavors are a bit more pronounced than the scent, but they're perhaps less interesting. you're met with roasted malts and orange, but the flavors don't pop, at all, and they're combined with muddy, earthy tones that becomes cloyingly sweet as the sip progresses. this beer needs something else. hops, perhaps? perhaps not, it's simply unbalanced.  given the wispy head, i wasn't 

Batch start index: 352 | Loss: 3.828625440597534
Time elapsed: 18.09360909461975
Actual Review: a - pours a hazy burnt orange. a billowy 3 finger head. average lacing.  s - big citrus aroma, caramel, hints of alcohol, dried herbs.  t - citrus hops with some strawberry fruitiness. some floral spice in the back fades into toasted caramel malt. the malt has a nice sweetness that keeps the hops from taking over everything.   the malt seems shy at first but opens up as you go. my first ipa out of a can. very easy drinking. good stuff!
Predicted Review: )))999hhh 9w9v vv9899w 99h  ww.9w98   h  9u96  9wh9    .9w wh 9w9  9  9.99 9999 j99  hh 9whh  u99wh     9     9969w hh h 69 h   9v hu .99v9999  hh 9vhh 9u   9 h  9  h  uwhh 96hh       .9 h  96 hh  9 h uw9  9   98w9 96w w 9   h96h     99wh    9    .96  9    9v  9w99 9w9  ww     9    9 mw9 96  9vhh 96hh 96    9999wh9w wh     9.999vv 9    9 ww  9  v99 96 h  999v99h.w 99h9w 9v99999.9  96 h  9 h 999v9969w99ww.99wh 99w  9 h     9.999h 9  v6666ua,,,

Batch start index: 480 | Loss: 3.7737877368927
Time elapsed: 24.859211444854736
Actual Review: a: pours a hazy orangereddish with a soapy, foamy head. lots of bubbles of small carbonation.  s: pine, citrus, and grapefruit all the way, almost to the point of smelling like a fresca! (how's that for an obscure reference). the malt is also noticeable in the form of a little fruitness.  t: wow! the hops pack a whallop both in the nose and in the finish of the taste, but the sweet malt coats the tongue and the throat and balances out nicely. the aftertaste of so many hops does take down the mouthfeel a bit, but the taste is definitely...tasty!!!  m: the hops sting a bit, even in the mouthfeel, but the malt is moderately thick, which helps wash everything down. the only drawback i can see is that the hops stick around so much in the aftertaste. it wants me to drink more, but it still is a little surprising.  d: this is a good ipa. almost like a firestone pale ale supercharged; the hops are fr

...

Actual Review: a- pours a cloudy reddish brown with a small head and some lacing  s- wow - the spices in this come in the nose very quickly and are very apparent - nutmeg, gingerbread, vanilla  t- like the nose - very delici8ous - ginger, cinnamin, vanilla, some slight citrus  m- medium bodied- creamy - could be a bit thicker.  d- i'm going to call this the best xmas ale i've had this season - fantastic beer.
Predicted Review: a- pours a cloudy reddish brown with a small head and some lacing  s- wow - the spices in this come in the nose very zuickly and are very apparent - nutmeg, gingerbread, vanilla  t- like the nose - very delicious - ginger, cinnamin, vanilla, some slight citrus  m- medium bodied- creamy - could be a bit thicker.  d- i'm going to call this the best xmas ale i've had this season - fantastic beer.;
Batch start index: 288 | Loss: 0.06368101388216019
Time elapsed: 3511.521584749222
Actual Review: bottle  palmer's beverage center columbus, oh  ruby red and crimson with 

Actual Review: 22 oz bottle served in a snifter. (review from notes of 5711)  pours a viscous, used motor oil black, yielding a small mocha-toned head. retention was (unsurprising) so-so; lacing in patches.  nose is very nice but i'd stop short of calling it exceptional. offers notes of chocolate, roasted malt, vanilla, and bourbon.  more of the same pull through in the flavor. bitter chocolate, roastiness, bourbon, a bit of vanilla, and a touch of booze in the finish. really good.  full bodied mouthfeel with adequate carbonation.  overall this is a fantastic beer. i wouldn't put it up there with my favorite -bal aged stouts - in fact i might not even prefer it to regular b.o.r.i.s. - but a damn tasty beer nonetheless.
Predicted Review:  oz bottle served in a snifter. zreview from notes of x'11)  pours a viscous, used motor oil black, yielding a small mocha-toned head. retention was -unsurprising) so-sox lacing in patches.  nose is very nice but i'd stop short of calling it exceptional

Actual Review: 22oz bomber purchased for $15.99 at deciccio's in ardsley, ny.  appearance: opaque brown black oil slick with a brownish slightly grape 1 finger rocky foam head that dissipates quickly and leaves mild amounts of lacing.  smell: mainly whisky barrel over roasted coffee with some caramelish sweetness and oats.  taste: over roasted malts couple with some chocolate bitterness and coffee flavor. oatmeal is a bit masked compared to the non-ba version. the whisky barrel adds a touch of heat and a sweet tinge that really awakens this ris.  mouthfeel: the oats really add silky smooth softness to this brew that i find very enjoyable. honestly this ris has one of the better mouthfeels for the style in my humble opinion.  drinkability: very drinkable for the style.
Predicted Review: oz bomber purchased for -1z. at deciccio's in ardsley, ny.  appearance: opazue brown black oil slick with a brownish slightly grape 1 finger rocky foam head that dissipates 'uickly and leaves mild amount

Actual Review: notes from 110211  *bomber w a 10oz nonic   a: pours a shiny black licorice color with a sort of lighter crimson edge to it. almost no head but just a rim of turbinado sugar color foam on topmaybe half a finger at most with low retention and some dotted lace. just dark and oily looking.   s: smells a bit woody with an earth and spice mix going on. vanilla beans, caramelized malts, and a hint of chocolate. some alcohol aromas exude. really rather complex array of aromas here.   t: wow this is a big robust stout with lots going on. tastes of charred roasty grains, earthy, with a distinct whisky note. a touch harsh but the whisky barrel treatment is rather subtle and not completely overbearing here. dark chocolates. slightly sweeter with some hints of vanilla. hops start midway and spike the back of the palate bringing a sort of dark fruit component to the brew. a little bit of alcohol heat and a dry roast coffee aftertaste.  m: has a rather smooth mouthfeel overall. medium

Actual Review: sampled at the cleveland beer fest 51411. poured black with a tan colored head that has enough carbonation to leave a small ring that lasts. notes of, whiskey, and heavily roasted malt and burnt chocolate fill the nose. this is a full bodied stout with yeast flavors enhanced by malt, burnt chocolate, coffee and a lingering hint of hop on finish. a little hot on the alcohol. i would love to let a bottle sit for a year or so.
Predicted Review: sampled at the cleveland beer fest x111' poured black with a tan colored head that has enough carbonation to leave a small ring that lasts. notes of, whiskey, and heavily roasted malt and burnt chocolate fill the nose. this is a full bodied stout with yeast flavors enhanced by malt, burnt chocolate, coffee and a lingering hint of hop on finish. a little hot on the alcohol. i would love to let a bottle sit for a year or so.;
Batch start index: 832 | Loss: 0.06039432808756828
Time elapsed: 3533.7661118507385
Actual Review: received thi

In [14]:
'''
train(model, X_train, y_train, X_valid, y_valid, cfg) # Train the model
outputs = generate(model, X_test, cfg) # Generate the outputs for test data
save_to_file(outputs, out_fname) # Save the generated outputs to a file
'''